# Stringmatching mit RapidFuzz
Um die identifizierten Sentiments und Unternehmen zuordnen zu können, wird das Attribut **companies** aus der StagingDB, welches nach der NER hinzugefügt wurde mit den Namenseinträgen der **companies-collection** aus der StagingDB verglichen. \
Da ein reines String-Matching nicht zielführend ist bzw. nicht alle Abwabdlungen von Firmennamen in der StagingDB vorhanden sind, wird mit der RapidFuzz-Bibliothek und einem Unschärfemaß gearbeitet.

In [1]:
import json
import pandas as pd
import aki_prj23_transparenzregister.utils.mongo.connector as conn
from aki_prj23_transparenzregister.config.config_providers import JsonFileConfigProvider
import aki_prj23_transparenzregister.utils.mongo.news_mongo_service as news
import aki_prj23_transparenzregister.utils.mongo.company_mongo_service as comps

In [ ]:
  self.config_provider = JsonFileConfigProvider("./secrets.json")
self.connect_string = self.config_provider.get_mongo_connection_string()
        self.connect_string.database = "transparenzregister_ner"
        self.connector = conn.MongoConnector(self.connect_string)

In [2]:
# Mongo Connect: create connection string and connect
config_provider = JsonFileConfigProvider("../../secrets.json")
engine = config_provider.get_mongo_connection_string()
engine.database = "transparenzregister_ner"
connector = conn.MongoConnector(engine)

In [3]:
# Process all documents and check if attribute 'name' is existing

# Read data from database
CompsObj = comps.CompanyMongoService(connector)
allComps = CompsObj.get_all()

# Create a cursor which has all unprogressed articles; articles without the attribute 'companies'
CursorCompNames = CompsObj.collection.find({"name": {"$exists": True}})
documents = list(CursorCompNames)

In [4]:
# create a list with all company names
compList = []

if len(documents) > 0:
    for document in documents:
        # ents=NERService.NERCompanyList(company_list,document)
        compList.append(document["name"])
        # add a new attribute 'companies' to document
        # newsObj.collection.update_one(
        #        {"_id": document["_id"]},  # Filter für das entsprechende Dokument
        #        {"$set": {"companies": ents}}  # Neues Attribut hinzufügen, initialisiert mit einer leeren Liste
        #    )

else:
    print("No documents found.")

In [5]:
# install and import rapidfuzz
# pip install rapidfuzz
from rapidfuzz import process

In [6]:
# Process all documents in news collection and check if attribute 'companies' is existing

# Read data from database
NERObj = news.MongoNewsService(connector)
allNER = NERObj.get_all()

# Create a cursor which has all unprogressed articles; articles without the attribute 'companies'
CursorNERNames = NERObj.collection.find({"companies": {"$exists": True}})
documentsNER = list(CursorNERNames)

In [9]:
#

if len(documentsNER) > 0:
    for document in documentsNER:
        resList = []  # result list with matched names
        for entity_name, frequency in document["companies"].items():
            if len(entity_name) > 2:
                result = process.extractOne(entity_name, compList)

                # Wenn ein ähnlicher Name gefunden wurde
                if (
                    result[1] >= 95
                ):  # Passen Sie die Ähnlichkeitsbewertungsschwelle nach Bedarf an
                    similar_name = result[0]
                    # print(f"Ähnlicher Name gefunden: {entity_name} (Ähnlichkeit: {result[1]})")
                    # print(f"Ähnlichkeit mit: {similar_name}")
                    # print(f"Häufigkeit: {frequency}")
                    print(
                        f"NER Entität: {entity_name} passt zu:{similar_name} zu: {result[1]}% und {frequency} Matches "
                    )

        # ents=NERService.NERCompanyList(company_list,document)
        # compList.append(document['name'])
        # add a new attribute 'companies' to document
        # newsObj.collection.update_one(
        #        {"_id": document["_id"]},  # Filter für das entsprechende Dokument
        #        {"$set": {"companies": ents}}  # Neues Attribut hinzufügen, initialisiert mit einer leeren Liste
        #    )

else:
    print("No documents found.")

NER Entität: Brenntag passt zu:Brenntag SE zu: 95.0% und 2 Matches 
NER Entität: Zalando passt zu:Zalando SE zu: 95.0% und 1 Matches 
NER Entität: Covestro passt zu:Covestro AG zu: 95.0% und 1 Matches 
NER Entität: United Internet passt zu:United Internet AG zu: 95.0% und 1 Matches 
NER Entität: Covestro passt zu:Covestro AG zu: 95.0% und 3 Matches 
NER Entität: Wacker Chemie passt zu:Wacker Chemie AG zu: 95.0% und 1 Matches 
NER Entität: Deutsche Post passt zu:Deutsche Post AG zu: 95.0% und 2 Matches 
NER Entität: Deutsche Post passt zu:Deutsche Post AG zu: 95.0% und 6 Matches 
NER Entität: Deutsche Post AG passt zu:Deutsche Post AG zu: 100.0% und 1 Matches 
NER Entität: Mercedes-Benz passt zu:Mercedes-Benz AG zu: 95.0% und 1 Matches 
NER Entität: Covestro passt zu:Covestro AG zu: 95.0% und 2 Matches 
NER Entität: Covestro passt zu:Covestro AG zu: 95.0% und 1 Matches 
NER Entität: Mercedes-Benz passt zu:Mercedes-Benz AG zu: 95.0% und 1 Matches 
NER Entität: Zalando passt zu:Zalando SE

In [22]:
documentsNER[1]["companies"].items()

dict_items([('Intel', 6), ('EU', 2), ('Reuters', 1), ('FPD', 1), ('Handelsblatts', 1), ('Weltspiegel', 1)])

In [30]:
compList

['0 10 24 Telefondienste GmbH',
 '1. Staiger Grundstücksverwaltung GmbH & Co. KG',
 '1 A Autenrieth Kunststofftechnik GmbH & Co. KG',
 '01050.com GmbH',
 '2. Schaper Objekt GmbH & Co. Kiel KG',
 'AASP Filmproduktionsgesellschaft mbH & Co. Leonie KG',
 'AgroMyc-Merck GmbH',
 'August Schäffler Verwaltungs GmbH',
 'AURELIUS Advisory AG',
 'AURELIUS Development Fourty-One GmbH',
 'AURELIUS Development Thirty-Four GmbH',
 'Aurelius Immo GmbH',
 'Aurelius Ulmenhof GmbH',
 '1&1 De-Mail GmbH',
 '1&1 Mail & Media Applications SE',
 '1&1 Telecommunication SE',
 '1&1 Telecom Service Montabaur GmbH',
 'A 1 Marketing, Kommunikation und neue Medien GmbH',
 'Admenta Deutschland GmbH',
 'AKF Bau UG (haftungsbeschränkt)',
 'Albert Henkel Verwaltungs-GmbH',
 'Ampero GmbH',
 'ATESTEO Beteiligungs GmbH',
 'Auda EnBW MA Initiatoren GmbH & Co. KG',
 'AURELIUS Development Eleven GmbH',
 'AURELIUS Development Fifteen GmbH',
 'AURELIUS Development Thirty-Two GmbH',
 'Aurelius Invest UG (haftungsbeschränkt)',
 

In [32]:
import re


# Funktion zum Entfernen von Unternehmenstypen und rechtlichen Zusätzen
def remove_legal_additions(name):
    # Verwenden Sie einen regulären Ausdruck, um gängige Zusätze wie "GmbH" und "AG" zu entfernen
    cleaned_name = re.sub(r"\b(GmbH|AG|KG|mbH & Co\. KG)\b", "", name)
    # Entfernen Sie führende und nachfolgende Leerzeichen
    cleaned_name = cleaned_name.strip()
    return cleaned_name


# Bereinigen Sie die Liste von Unternehmensnamen
cleaned_company_names = [remove_legal_additions(name) for name in compList]

In [33]:
cleaned_company_names

['0 10 24 Telefondienste',
 '1. Staiger Grundstücksverwaltung  & Co.',
 '1 A Autenrieth Kunststofftechnik  & Co.',
 '01050.com',
 '2. Schaper Objekt  & Co. Kiel',
 'AASP Filmproduktionsgesellschaft mbH & Co. Leonie',
 'AgroMyc-Merck',
 'August Schäffler Verwaltungs',
 'AURELIUS Advisory',
 'AURELIUS Development Fourty-One',
 'AURELIUS Development Thirty-Four',
 'Aurelius Immo',
 'Aurelius Ulmenhof',
 '1&1 De-Mail',
 '1&1 Mail & Media Applications SE',
 '1&1 Telecommunication SE',
 '1&1 Telecom Service Montabaur',
 'A 1 Marketing, Kommunikation und neue Medien',
 'Admenta Deutschland',
 'AKF Bau UG (haftungsbeschränkt)',
 'Albert Henkel Verwaltungs-',
 'Ampero',
 'ATESTEO Beteiligungs',
 'Auda EnBW MA Initiatoren  & Co.',
 'AURELIUS Development Eleven',
 'AURELIUS Development Fifteen',
 'AURELIUS Development Thirty-Two',
 'Aurelius Invest UG (haftungsbeschränkt)',
 'AEMtec',
 'AIB Verwaltungs',
 'AK-ON Haustechnik e.K. Inh. Musa Akkaya',
 'Alb-Windkraft  & Co.',
 'AL GRAMM',
 'Anneliese